# Infer Pooled Model Parameters from Individuals in Lung Cancer Treatement Group with Medium Erlotinib Dose

## Show control group data

In [1]:
import os

import pandas as pd

import erlotinib as erlo


# Get data
data = erlo.DataLibrary().lung_cancer_medium_erlotinib_dose_group()

# Create scatter plot
fig = erlo.plots.PKTimeSeriesPlot()
fig.add_data(data, id_key='#ID', time_key='TIME in day', biom_key='PLASMA CONCENTRATION in mg/L', dose_key='DOSE in mg')
fig.set_axis_labels(time_label=r'$\text{Time in day}$', biom_label=r'$\text{Plasma conc. in mg/L}$', dose_label=r'$\text{Dose in mg}$')

# Show figure
fig.show()

**Figure 1:** To be completed

## Find MAP estimates for pooled model parameters

In [3]:
import numpy as np
import pints


# Define model
path = erlo.ModelLibrary().one_compartment_pk_model()
model = erlo.PharmacokineticModel(path)
model.set_administration(compartment='central', direct=False)
model.set_dosing_regimen(dose=0.65, start=3, period=1, num=13)  # TODO: Dose should be taken from dataset
model.set_parameter_names(names={
    'central.drug_amount': 'Central comp. drug amount in mg',
    'dose.drug_amount': 'Dose comp. drug amount in mg',
    'central.size': 'Volume of distribution in L',
    'dose.absorption_rate': 'Absorption rate in 1/day',
    'myokit.elimination_rate': 'Elimination rate in 1/day'})

# Find maximum a posteriori probability estimates (MAP)
log_likelihoods = []
ids = data['#ID'].unique()
for individual in ids:
    # Get data for individual
    mask = data['#ID'] == individual
    times = data[mask]['TIME in day'].to_numpy()
    observed_concs = data[mask]['PLASMA CONCENTRATION in mg/L'].to_numpy()

    # Create likelihoods for each individuals
    problem = erlo.InverseProblem(model, times, observed_concs)
    log_likelihoods.append(
        pints.ConstantAndMultiplicativeGaussianLogLikelihood(problem))

# Create pooled posterior
log_likelihood = pints.PooledLogPDF(log_pdfs=log_likelihoods, pooled=[True]*8)
log_prior_central_drug_amount = pints.UniformLogPrior(-1E-3, 1E-3)  # Fixed to zero below
log_prior_dose_drug_amount = pints.UniformLogPrior(-1E-3, 1E-3)  # Fixed to zero below
log_prior_volume = pints.HalfCauchyLogPrior(location=0, scale=3)
log_prior_absorption_rate = pints.HalfCauchyLogPrior(location=0, scale=3)
log_prior_elimination_rate = pints.HalfCauchyLogPrior(location=0, scale=3)
log_prior_sigma_base = pints.HalfCauchyLogPrior(location=0, scale=3)
log_prior_eta = pints.UniformLogPrior(1E-3, 1E3)  # Fixed to 1 below
log_prior_sigma_rel = pints.HalfCauchyLogPrior(location=0, scale=3)
log_prior = pints.ComposedLogPrior(
    log_prior_central_drug_amount, 
    log_prior_dose_drug_amount,
    log_prior_volume,
    log_prior_absorption_rate,
    log_prior_elimination_rate,
    log_prior_sigma_base,
    log_prior_eta,
    log_prior_sigma_rel)
log_posterior = pints.LogPosterior(log_likelihood, log_prior)

# Set up optmisation controller
optimiser = erlo.OptimisationController(log_posterior)

# Fix potency kappa, and drug concentration to 0, as well as eta to 1
# (This is the control group, and thus there is no drug)
optimiser.fix_parameters(
    mask=[True, True, False, False, False, False,True, False],
    values=[0, 0, 1])

# Run optimisation
map_estimates = optimiser.run()

# Label ID as pooled
map_estimates['ID'] = 'Pooled'

ValueError: Model has to be an instance of erlotinib.Pharmacodynamic.

### Visualise optimisation results

In [3]:
fig = erlo.plots.ParameterEstimatePlot()
fig.add_data(map_estimates)

fig.show()

Figure 2:

## Find posterior probability distribution

In [4]:
import numpy as np
import pints
from tqdm.notebook import tqdm


# Find posterior probability distributions
log_likelihoods = []
ids = data['#ID'].unique()
for individual in ids:
    # Get data for individual
    mask = data['#ID'] == individual
    times = data[mask]['TIME in day'].to_numpy()
    observed_volumes = data[mask]['TUMOUR VOLUME in cm^3'].to_numpy()

    # Create likelihoods for each individuals
    problem = erlo.InverseProblem(model, times, observed_volumes)
    log_likelihoods.append(
        pints.ConstantAndMultiplicativeGaussianLogLikelihood(problem))

# Create pooled posterior
log_likelihood = pints.PooledLogPDF(log_pdfs=log_likelihoods, pooled=[True]*8)
log_prior_tumour_volume = pints.HalfCauchyLogPrior(location=0, scale=3)
log_prior_drug_conc = pints.UniformLogPrior(-1E-3, 1E-3)  # Fixed to zero below
log_prior_kappa = pints.UniformLogPrior(-1E-3, 1E-3)  # Fixed to zero below
log_prior_lambda_0 = pints.HalfCauchyLogPrior(location=0, scale=3)
log_prior_lambda_1 = pints.HalfCauchyLogPrior(location=0, scale=3)
log_prior_sigma_base = pints.HalfCauchyLogPrior(location=0, scale=3)
log_prior_eta = pints.UniformLogPrior(1E-3, 1E3)  # Fixed to 1 below
log_prior_sigma_rel = pints.HalfCauchyLogPrior(location=0, scale=3)
log_prior = pints.ComposedLogPrior(
    log_prior_tumour_volume, 
    log_prior_drug_conc,
    log_prior_kappa,
    log_prior_lambda_0,
    log_prior_lambda_1,
    log_prior_sigma_base,
    log_prior_eta,
    log_prior_sigma_rel)
log_posterior = pints.LogPosterior(log_likelihood, log_prior)

# Set up optmisation controller
sampler = erlo.SamplingController(log_posterior)

# Fix potency kappa, and drug concentration to 0, as well as eta to 1
# (This is the control group, and thus there is no drug)
sampler.fix_parameters(
    mask=[False, True, True, False, False, False,True, False],
    values=[0, 0, 1])

# Set initial parameters to map estimates
sampler.set_initial_parameters(data=map_estimates)

# Run sampler
posterior_samples = sampler.run(n_iterations=5000)

# Label samples as pooled
posterior_samples['ID'] = 'Pooled'

Using Haario adaptive covariance MCMC
Generating 10 chains.
Running in parallel with 8 worker processess.
Iter. Eval. Accept.   Accept.   Accept.   Accept.   Accept.   Accept.   Accept.   Accept.   Accept.   Accept.   Time m:s
0     10     0         0         0         0         0         0         0         0         0         0          0:00.1
1     20     0         0         0         0         0         0         0         0         0         0          0:00.1
2     30     0         0         0         0         0         0         0         0         0         0          0:00.1
3     40     0         0         0         0         0         0         0         0         0         0          0:00.1
Initial phase completed.
500   5010   0.152     0.154     0.16      0.166     0.188     0.164     0.146     0.18      0.16      0.192      0:09.7
1000  10010  0.167     0.165     0.171     0.175     0.182     0.177     0.161     0.178     0.171     0.19       0:19.2
1500  15010  0.164    

In [5]:
fig = erlo.plots.MarginalPosteriorPlot()
fig.add_data(data=posterior_samples, warm_up_iter=2500)

fig.show()

Figure 3